# 💥  Kokora TTS 2+ mins in few seconds on T4 Colab 💥

# 1️⃣ Install dependencies silently


In [1]:
!git lfs install
!git clone https://huggingface.co/hexgrad/Kokoro-82M
%cd Kokoro-82M
!apt-get -qq -y install espeak-ng > /dev/null 2>&1
!pip install -q phonemizer torch transformers scipy munch


Git LFS initialized.
Cloning into 'Kokoro-82M'...
remote: Enumerating objects: 140, done.
remote: Counting objects: 100% (136/136), done.
remote: Compressing objects: 100% (136/136), done.
remote: Total 140 (delta 63), reused 0 (delta 0), pack-reused 4 (from 1)
Receiving objects: 100% (140/140), 60.13 KiB | 20.04 MiB/s, done.
Resolving deltas: 100% (63/63), done.
Filtering content: 100% (17/17), 820.18 MiB | 59.56 MiB/s, done.
/content/Kokoro-82M
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 48.2/48.2 kB 2.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 162.6/162.6 kB 9.2 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 103.8/103.8 kB 10.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.7/1.7 MB 43.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 59.9/59.9 kB 5.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 213.4/213.4 kB 20.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━

# 2️⃣ Build the model and load the default voicepack


In [2]:
from models import build_model
import torch
device = 'cuda' if torch.cuda.is_available() else 'cpu'
MODEL = build_model('kokoro-v0_19.pth', device)
VOICE_NAME = [
    'af', # Default voice is a 50-50 mix of Bella & Sarah
    'af_bella', 'af_sarah', 'am_adam', 'am_michael',
    'bf_emma', 'bf_isabella', 'bm_george', 'bm_lewis',
    'af_nicole', 'af_sky',
][8]
VOICEPACK = torch.load(f'voices/{VOICE_NAME}.pt', weights_only=True).to(device)
print(f'Loaded voice: {VOICE_NAME}')


/usr/local/lib/python3.11/dist-packages/torch/nn/utils/weight_norm.py:143: FutureWarning: `torch.nn.utils.weight_norm` is deprecated in favor of `torch.nn.utils.parametrizations.weight_norm`.
  WeightNorm.apply(module, name, dim)
/usr/local/lib/python3.11/dist-packages/torch/nn/modules/rnn.py:123: UserWarning: dropout option adds dropout after all but last recurrent layer, so non-zero dropout expects num_layers greater than 1, but got dropout=0.2 and num_layers=1
  warnings.warn(


Loaded voice: bm_lewis


# 3️⃣ Call generate, which returns 24khz audio and the phonemes used


In [3]:
text = '''Put simply, AI agents are artificial intelligence that use tools to accomplish goals. AI agents have the ability to remember across tasks and changing states; they can use one or more AI models to complete tasks; and they can decide when to access internal or external systems on a user’s behalf. This enables AI agents to make decisions and take actions autonomously with minimal human oversight.

For example, a consumer goods company wanted to optimize its global marketing campaigns using an AI agent to transform processes. A project that once required six analysts per week now required a single employee working with an agent, delivering results in under an hour. Here’s how it works:

AI agent gathers data: On a weekly basis, the agent autonomously gathers and joins marketing data via connected data pipelines.
AI agent analyzes performance: The agent performs contextual analysis on the data to understand campaign performance metrics and compare against expectations, receiving business context from an operator when necessary.
AI agent offers recommendations: The agent writes a standardized report that proposes optimizations. An operator stress tests and refines the AI agent’s recommendations as needed.
AI agent updates platforms: When given human approval, the agent updates media buying platforms with the recommendations.'''

In [4]:
from kokoro import generate

# Language is determined by the first letter of the VOICE_NAME:
# 🇺🇸 'a' => American English => en-us
# 🇬🇧 'b' => British English => en-gb


audio = []
for chunk in text.split("."):
    print(chunk)
    if len(chunk) < 2:
        # a try except block for non verbalizable text is probably better than this hack
        continue
    snippet, _ = generate(MODEL, chunk, VOICEPACK, lang=VOICE_NAME[0])
    audio.extend(snippet)


Put simply, AI agents are artificial intelligence that use tools to accomplish goals
 AI agents have the ability to remember across tasks and changing states; they can use one or more AI models to complete tasks; and they can decide when to access internal or external systems on a user’s behalf
 This enables AI agents to make decisions and take actions autonomously with minimal human oversight


For example, a consumer goods company wanted to optimize its global marketing campaigns using an AI agent to transform processes
 A project that once required six analysts per week now required a single employee working with an agent, delivering results in under an hour
 Here’s how it works:

AI agent gathers data: On a weekly basis, the agent autonomously gathers and joins marketing data via connected data pipelines



AI agent analyzes performance: The agent performs contextual analysis on the data to understand campaign performance metrics and compare against expectations, receiving business context from an operator when necessary

AI agent offers recommendations: The agent writes a standardized report that proposes optimizations


 An operator stress tests and refines the AI agent’s recommendations as needed

AI agent updates platforms: When given human approval, the agent updates media buying platforms with the recommendations



# 4️⃣ Display the 24khz audio and print the output phonemes


In [5]:
from IPython.display import display, Audio
display(Audio(data=audio, rate=24000, autoplay=True))